In [1]:
import optuna
from optuna import Trial

from math import sqrt
from typing import Tuple, List

import numpy as np
import pandas as pd
from mordred import Calculator, descriptors
#import openbabel
from openbabel import pybel
from PyBioMed.PyMolecule.fingerprint import CalculatePubChemFingerprint,CalculateECFP2Fingerprint
from rdkit import Chem
from rdkit.Chem.rdchem import Atom

from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split

from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score, confusion_matrix, matthews_corrcoef, roc_curve, auc 
from sklearn.metrics import precision_recall_curve


from torch_geometric.data import Data
from torch_geometric.loader import DataLoader as G_Loader 
from torch_geometric.nn import GCNConv, GATConv
from torch_geometric.nn import global_mean_pool
from torch_geometric.nn import BatchNorm


# RDkit
from rdkit import Chem
from rdkit.Chem.rdmolops import GetAdjacencyMatrix
# Pytorch and Pytorch Geometric
import torch

import torch.nn as nn
from torch.nn import Linear
import torch.optim as optim
import torch.nn.functional as F # activation function
from torch.utils.data import Dataset
from torch.utils.data import DataLoader as V_Loader # dataset management

from sklearn.metrics import accuracy_score, confusion_matrix, matthews_corrcoef, roc_curve, auc 
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import cohen_kappa_score
from sklearn.metrics import roc_auc_score

# performances visualization 
import matplotlib.pyplot as plt
#import seaborn as sns
import statistics
from prettytable import PrettyTable
%run ./my_performances.ipynb 


#%run ./graph_feature.ipynb 
#%run ./dataset_processing.ipynb 

C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# reload the data fingerprint 
#=======================================================
k=10
final_clean_fingerp_train=[]
final_clean_fingerp_val=[]
for i in range(k):
    final_clean_fingerp_train.append(np.load('final_clean_fingerp_train'+ str(i)+'.npy'))
    final_clean_fingerp_val.append(np.load('final_clean_fingerp_val' +str(i)+'.npy'))

final_clean_fingerp_test = np.load('final_clean_fingerp_test.npy')

In [3]:
len(final_clean_fingerp_val[0])

126

In [4]:
len(final_clean_fingerp_train[0])

1132

In [5]:
len(final_clean_fingerp_test)

315

In [6]:
train_idx = np.load('train_indices.npy')
val_idx = np.load('val_indices.npy')
test_idx = np.load('test_indices.npy')

In [7]:
# load the output label 
total_train_targets =[]
total_validation_targets =[]
total_test_targets=[]
for i in range(k):
    total_train_targets.append(np.load('total_train_targets'+ str(i)+'.npy'))
    total_validation_targets.append(np.load('total_validation_targets' +str(i)+'.npy'))

total_test_targets= np.load('total_test_targets.npy')

In [8]:
len(total_validation_targets[0])

126

In [9]:
# create dataloader for training (vector data)
#======================================================================================
list_data_fingerp_train =[]
list_data_fingerp_val =[]
list_data_target_train =[]
list_data_target_val =[]

for data_train, data_val, tr_targets, val_targets in zip(final_clean_fingerp_train, final_clean_fingerp_val,total_train_targets, total_validation_targets):
    train_loader = V_Loader(dataset = data_train, batch_size = 126)
    val_loader = V_Loader(dataset = data_val, batch_size = 126)
    
    tr_target_loader = V_Loader(dataset = tr_targets, batch_size = 126)
    val_target_loader =  V_Loader(dataset = val_targets, batch_size = 126)
    
    list_data_fingerp_train.append(train_loader)
    list_data_fingerp_val.append(val_loader)
    
    list_data_target_train.append(tr_target_loader)
    list_data_target_val.append(val_target_loader)

In [10]:
# load structured graph data
train_idx = np.load('train_indices.npy')
val_idx = np.load('val_indices.npy')
test_idx = np.load('test_indices.npy')

k=10
data_list_train=[]
for i in range(k):
    one_fold= []
    for idx in range(train_idx[i]):
        one_graph_data =torch.load(f"data_train_{i}/tensor{idx}.pt")
        one_fold.append(one_graph_data)
    data_list_train.append(one_fold)
    
data_list_val=[]
for i in range(k):
    one_fold= []
    for idx in range(val_idx[i]):
        one_graph_data =torch.load(f"data_val_{i}/tensor{idx}.pt")
        one_fold.append(one_graph_data)
    data_list_val.append(one_fold)
    
data_list_test =[]
for idx in range(test_idx):
    one_graph_data =torch.load(f"data_test/tensor{idx}.pt")
    data_list_test.append(one_graph_data)
    
# load the output label 
total_train_targets =[]
total_validation_targets =[]
total_test_targets=[]
for i in range(k):
    total_train_targets.append(np.load('total_train_targets'+ str(i)+'.npy'))
    total_validation_targets.append(np.load('total_validation_targets' +str(i)+'.npy'))

total_test_targets= np.load('total_test_targets.npy')

In [11]:
# create dataloader for training (graph data)
#======================================================================================
list_data_graph_train =[]
list_data_graph_val =[]
for data_train, data_val in zip(data_list_train, data_list_val):
    train_loader = G_Loader(dataset = data_train, batch_size = 126)
    val_loader = G_Loader(dataset = data_val, batch_size = 126)
    list_data_graph_train.append(train_loader)
    list_data_graph_val.append(val_loader)

# create dataloader for test (graph data)
#======================================================================================
g_test_loader = G_Loader(dataset = data_list_test, batch_size = 1)

In [12]:
#criterion = torch.nn.CrossEntropyLoss()
#define the loss function 
criterion = torch.nn.BCELoss()

In [13]:
# input for forward the model x, edge_attr, edge_index, batch_index
def train_1(g_loader,f_loader, combined_model, optimizer):
    combined_model.train()
    
    for data_X1, data_X2 in zip(g_loader, f_loader):  # Iterate in batches over the training dataset.
        
        out = combined_model(data_X1.x, data_X1.edge_index, data_X1.batch, 
                             torch.tensor(data_X2, dtype=torch.float32))  # Perform a single forward pass.
        
        y_t = data_X1.y.type(torch.FloatTensor)
        loss = criterion(out[:,0], y_t)  # Compute the loss.
        #print(k)
        #print(loss)
        loss.backward()  # Derive gradients.
        optimizer.step()  # Update parameters based on gradients.
        optimizer.zero_grad()  # Clear gradients.
    return loss, combined_model, optimizer

def validation_1(g_loader,f_loader,combined_model):
    for data_X1, data_X2 in zip(g_loader,f_loader): # Iterate in batches over the training dataset.
        out = combined_model(data_X1.x, data_X1.edge_index, data_X1.batch, 
                             torch.tensor(data_X2, dtype=torch.float32))  # Perform a single forward pass.
        
        y_t = data_X1.y.type(torch.FloatTensor)
        val_loss = criterion(out[:,0], y_t)  # Compute the loss.
        
    return val_loss

In [14]:
def test_1(g_loader,f_loader,combined_model):
    combined_model.eval()
    list_pred =[]
    list_targets =[]
    correct = 0
    for data_X1, data_X2 in zip(g_loader,f_loader): # Iterate in batches over the training dataset.
        out = combined_model(data_X1.x, data_X1.edge_index, data_X1.batch, 
                             torch.tensor(data_X2, dtype=torch.float32))  # Perform a single forward pass.
        out_1 = out[:,0] 
        list_pred.append(out_1.item())
        list_targets.append(data_X1.y.item())
    return list_pred, list_targets 

# used to count the train accuracy ,and validation accuracy when in the training mode 
def test(g_loader,f_loader,combined_model):
    combined_model.eval()

    correct = 0
    for data_X1, data_X2 in zip(g_loader,f_loader): # Iterate in batches over the training dataset.
        out = combined_model(data_X1.x, data_X1.edge_index, data_X1.batch, 
                             torch.tensor(data_X2, dtype=torch.float32))  # Perform a single forward pass.
        out_1 = out[:,0]
        for i,value in enumerate(out_1) :
            if value > 0.5 :
                out_1[i] = 1
            else : out_1[i] = 0
        pred = out_1  # Use the class with highest probability.
        correct += int((pred == data_X1.y).sum())  # Check against ground-truth labels.
    return correct / len(g_loader.dataset)  # Derive ratio of correct predictions.

In [15]:
def get_optimizer(gnn_model, learning_rate, optimizer_type, weight_decay=1e-4):
    if optimizer_type==1:
        optimizer = torch.optim.SGD(gnn_model.parameters(), lr=learning_rate, momentum=0.9)
    if optimizer_type==2:
        optimizer = torch.optim.Adam(gnn_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
    if optimizer_type ==3 :
        optimizer = torch.optim.Adamax(gnn_model.parameters(), lr=learning_rate, betas=(0.9, 0.999), eps=1e-08, weight_decay=1e-4)
        
    return optimizer

In [16]:
class modelA(torch.nn.Module):
    def __init__(self, hidden_channels1,hidden_channels2, num_node_features,heads1,heads2
                 ,dropout_rateA,dropout_rateB, dropout_rateC,dense_layer1):
        super(modelA, self).__init__()
        
        torch.manual_seed(12345)
        self.conv1 = GATConv(num_node_features, hidden_channels1,heads1)
        self.conv2 = GATConv(hidden_channels1*heads1,hidden_channels2, heads2)
        
        self.bn1 = BatchNorm (hidden_channels1*heads1)
        self.bn2 = BatchNorm (hidden_channels2*heads2)
        
        self.dropoutA = dropout_rateA
        self.dropoutB = dropout_rateB
        self.dropoutC = dropout_rateC
        
        self.lin1 = Linear(hidden_channels2*heads2,dense_layer1)
        #self.lin1 = Linear(hidden_channels2*heads2,dense_layer1)
        self.lin2=  Linear(dense_layer1,1)
        
    def forward(self, x, edge_index, batch):

        x = self.conv1(x, edge_index)
        
        x = F.dropout(x, p=self.dropoutA , training=self.training)
        x = x.relu()
        x = self.bn1(x)
        x = self.conv2(x, edge_index)
        
        x = F.dropout(x, p=self.dropoutB , training=self.training)
        x = x.relu()
        x = self.bn2(x)  
        
        # 2. Readout layer
        x = global_mean_pool(x, batch)  # [batch_size, hidden_channels]
        x = self.lin1(x)
        x = F.dropout(x, p=self.dropoutC , training=self.training)
        x = x.relu()
        x = self.lin2(x)
        return torch.sigmoid(x)


class modelB(torch.nn.Module):
    def __init__(self, input_features, output_features,dropout_rateB1,dropout_rateB2,dropout_rateB3,  
                 dense_layer1,dense_layer2, dense_layer3):
        super(modelB, self).__init__()
        self.lin1 = nn.Linear(input_features,dense_layer1)
      
        self.lin2 = nn.Linear(int(dense_layer1), dense_layer2)
        self.lin3 = nn.Linear(int(dense_layer2), dense_layer3)
        self.lin4 = nn.Linear(int(dense_layer3), output_features)
        
        self.bn1 = nn.BatchNorm1d(int(dense_layer1))
        self.bn2 = nn.BatchNorm1d(int(dense_layer2))
        self.bn3 = nn.BatchNorm1d(int(dense_layer3))
        self.dropoutB1 = dropout_rateB1
        self.dropoutB2 = dropout_rateB2
        self.dropoutB3 = dropout_rateB3
        
    def forward(self, x):
        x = self.lin1(x)
        x = self.bn1(x)
       
        x = F.dropout(x, p= self.dropoutB1, training=self.training)
        x = x.relu()
  #      
        x = self.lin2(x)
        x = self.bn2(x)   
        x = F.dropout(x, p= self.dropoutB2, training=self.training)
        x = x.relu()
  #      
        x = self.lin3(x)
        x = self.bn3(x)   
        x = F.dropout(x, p= self.dropoutB3, training=self.training)

        x = x.relu()
        x = self.lin4(x)
        return torch.sigmoid(x)        
    
class Combined_model(nn.Module):
    def __init__(self, modelA, modelB, total_input_features, num_classes,dropout_rate_C, dense_layer_C):
        super(Combined_model, self).__init__()
        self.model_1 = modelA
        self.model_2 = modelB
        
        
        self.lin1 = Linear(total_input_features,int(dense_layer_C))
        self.lin2 = Linear(int(dense_layer_C),num_classes)
        
        self.dropout_C = dropout_rate_C
        
    def forward(self, x1,edge_index, batch, x2):
        xa = self.model_1(x1, edge_index, batch) # x1 node features in graph
        xb= self.model_2(x2)                     # x2 is a vector features 
  #      xc= self.model_3(x3)                     # x2 is a vector features 
        
        x = torch.cat((xa, xb), dim=1)
  #      x = torch.cat((x, xc), dim=1)
         # 3. Apply a final classifier
        x = self.lin1(x)
        x = F.dropout(x, p= self.dropout_C, training=self.training)
        x = x.relu()
        x = self.lin2(x)
        return torch.sigmoid(x)

In [17]:
hyper_param = {'dropout_rateB1': 0.19029920767006717,
               'dropout_rateB2': 0.12142154817498285,
               'dropout_rateB3': 0.30892320125476364,
               'dense_layer1'  : 180,
               'dense_layer2'  : 96,
               'dense_layer3'  : 40,
               'learning_rate' : 0.00014475405687104653,
               'weight_decay'  : 0.0001839631656485908}

In [18]:
# load all the model in the fold 
k =10
list_modelA = []
list_modelB = []

for i in range(k):
    
    input_features    = 166 # length of feature data vector 
    output_features   = 1
    
    dropout_rateB1 =hyper_param['dropout_rateB1']
    dropout_rateB2 =hyper_param['dropout_rateB2']
    dropout_rateB3 =hyper_param['dropout_rateB3']
    dense_layer1 = hyper_param['dense_layer1']
    dense_layer2 = hyper_param['dense_layer2']
    dense_layer3 = hyper_param['dense_layer3']
 
        
    model_b= modelB(input_features, output_features,dropout_rateB1,dropout_rateB2,dropout_rateB3,  
                 dense_layer1,dense_layer2, dense_layer3)
    PATH = '0.39289model_fingerp'+ str(i)+'.pth'
    model_b.load_state_dict(torch.load(PATH))
    
    for param in model_b.parameters():
        param.requires_grad = False

    list_modelB.append(model_b)
    

In [19]:
param_new ={'learning_rate': 0.00016244062674888418, 
            'weight_decay': 0.00013754366736300802, 
            'hidden_channels1 ': 82, 
            'hidden_channels2 ': 82, 
            'heads1': 9, 
            'heads2': 9, 
            'dropout_rate_C': 0.3054920980974637, 
            'dense_layer_C': 16}

In [28]:
list_data_vec_trainB = list_data_fingerp_train
list_data_vec_valB = list_data_fingerp_val

def objective(trial):
    
    k=10 # number of fold 
    # data for fingerprints , no need to be trained 
    input_features    = 166 # length of feature data vector 
   
    optimizer_type = 2
    learning_rate = trial.suggest_loguniform('learning_rate', 0.000140, 0.0001409)
    #learning_rate =0.00014084414187346615
    #weight_decay= trial.suggest_loguniform('weight_decay', 0.0001210, 0.0001219)
    weight_decay =  0.00012168710374149417
    # data for graph
    num_node_features =79
    #hidden_channels1  = trial.suggest_int('hidden_channels1',80,120, step=2) 
    
    #hidden_channels2  = trial.suggest_int('hidden_channels2',80,120, step=2) 
    #heads1  =trial.suggest_int('heads1',8,10, step=1) 
    #heads2  =trial.suggest_int('heads2',8,10, step=1) 
    #dropout_rateA = trial.suggest_uniform('dropout_rateA',  0.1, 0.5)
    #dropout_rateB = trial.suggest_uniform('dropout_rateB',  0.1, 0.5)
    #dropout_rateC = trial.suggest_uniform('dropout_rateC',  0.1, 0.5)
     
    #hidden_channels1 =trial.suggest_int('hidden_channels1 ',64,128, step=2) 
    hidden_channels1 =82
    
    #hidden_channels2 =trial.suggest_int('hidden_channels2 ',64,128, step=2) 
    hidden_channels2 =82
    
    num_node_features =79
    #heads1             = trial.suggest_int('heads1',8,10, step=1) 
    #heads2             = trial.suggest_int('heads2',8,10, step=1) 
    heads1             =9
    heads2             =9
    #dropout_rateA = trial.suggest_uniform('dropout_rateA',  0.1, 0.5)
    #dropout_rateB = trial.suggest_uniform('dropout_rateB', 0.1, 0.5)
    #dropout_rateC = trial.suggest_uniform('dropout_rateC', 0.1, 0.5)
    dropout_rateA = 0.20184714781996305
    dropout_rateB = 0.26157496401430025
    dropout_rateC = 0.12826012269932247    
    #dropout_rate_C = trial.suggest_uniform('dropout_rate_C', 0.1, 0.5)
    
    dense_layer1 = 64
    # data for combined 
    total_input_features = 2
    num_classes =1
    dropout_rate_C = 0.3054920980974637
    dense_layer_C = 16

    list_trained_model =[]
    list_val_acc=[]
    
    for i in range(k):
        model_a  = modelA(hidden_channels1,hidden_channels2, num_node_features,heads1,heads2
                 ,dropout_rateA,dropout_rateB, dropout_rateC,dense_layer1)
        
        model_b  = list_modelB[i] # model b is pretrained model trainable = off 
        
        combined_model = Combined_model(model_a, model_b, total_input_features, num_classes,dropout_rate_C, dense_layer_C)
        
        optimizer = get_optimizer(combined_model, learning_rate, optimizer_type,weight_decay)
   
   
        for epoch in range(1,50):
            
                
            train_loss,combined_model, optimizer = train_1(list_data_graph_train[i],list_data_vec_trainB[i],
                                                           combined_model,optimizer)
            val_loss                             = validation_1(list_data_graph_val[i], list_data_vec_valB[i],
                                                                combined_model) 
        
            train_acc                            = test(list_data_graph_train[i],list_data_vec_trainB[i],combined_model)
            val_acc                              = test(list_data_graph_val[i],list_data_vec_valB[i], combined_model)
        
        
            print(f'Fold: {i}')
            print(f'Epoch: {epoch:03d}, Train Loss: {train_loss.item():.4f}')
            print(f'Epoch: {epoch:03d}, Train Acc: {train_acc:.4f}')
            print(f'Epoch: {epoch:03d}, val Loss: {val_loss.item():.4f}')
            print(f'Epoch: {epoch:03d}, val Acc: {val_acc:.4f}')
            print(" ")
        
        list_trained_model.append(combined_model)
        
    nCV= 10 # ten crossfold validation 
    list_fold_pred =[]
    list_fold_targets =[]


    v_test_loader = V_Loader(dataset = final_clean_fingerp_test, batch_size = 1)

    g_test_loader = G_Loader(dataset = data_list_test, batch_size = 1)


    for combined_model in list_trained_model:  
        list_pred, list_targets = test_1(g_test_loader, v_test_loader,combined_model)
        list_fold_pred.append(list_pred)
        list_fold_targets.append(list_targets)
    
# GET THE PERFORMANCES FROM THE TEST
#========================================================================
    total_performances = performances(list_fold_pred, list_fold_targets, nCV)
    mcc = statistics.mean(total_performances[3])
    acc = statistics.mean(total_performances[0])
    print(" ")
    print(f'The average of mcc : {mcc}')
    
    if  acc> 0.75:
            for i, model in enumerate(list_trained_model):
                torch.save(model.state_dict(), str(acc)+"model_hybrid" +str(i)+ ".pth")
    return acc

In [ ]:
# start to optimize 
study = optuna.create_study(direction = 'maximize')
study.optimize(objective, n_trials=500)

study.best_params  

[I 2024-08-01 15:52:36,654] A new study created in memory with name: no-name-4f21fb11-dda5-4bb3-b97c-644bf16b6eb9
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  # This is added back by InteractiveShellApp.init_path()
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  if sys.path[0] == "":
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(Tru

Fold: 0
Epoch: 001, Train Loss:, 0.7914
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7604
Epoch: 001, val Acc: 0.3333
 
Fold: 0
Epoch: 002, Train Loss:, 0.7711
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7565
Epoch: 002, val Acc: 0.3333
 
Fold: 0
Epoch: 003, Train Loss:, 0.7595
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7525
Epoch: 003, val Acc: 0.3333
 
Fold: 0
Epoch: 004, Train Loss:, 0.7662
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss:, 0.7583
Epoch: 004, val Acc: 0.3333
 
Fold: 0
Epoch: 005, Train Loss:, 0.7699
Epoch: 005, Train Acc: 0.3330
Epoch: 005, val Loss:, 0.7451
Epoch: 005, val Acc: 0.3333
 
Fold: 0
Epoch: 006, Train Loss:, 0.7639
Epoch: 006, Train Acc: 0.3330
Epoch: 006, val Loss:, 0.7504
Epoch: 006, val Acc: 0.3333
 
Fold: 0
Epoch: 007, Train Loss:, 0.7606
Epoch: 007, Train Acc: 0.3330
Epoch: 007, val Loss:, 0.7376
Epoch: 007, val Acc: 0.3333
 
Fold: 0
Epoch: 008, Train Loss:, 0.7504
Epoch: 008, Train Acc: 0.3330
Epoch: 008, val Loss

Fold: 1
Epoch: 016, Train Loss:, 0.7307
Epoch: 016, Train Acc: 0.3330
Epoch: 016, val Loss:, 0.7256
Epoch: 016, val Acc: 0.3333
 
Fold: 1
Epoch: 017, Train Loss:, 0.7256
Epoch: 017, Train Acc: 0.3330
Epoch: 017, val Loss:, 0.7289
Epoch: 017, val Acc: 0.3333
 
Fold: 1
Epoch: 018, Train Loss:, 0.7197
Epoch: 018, Train Acc: 0.3330
Epoch: 018, val Loss:, 0.7119
Epoch: 018, val Acc: 0.3333
 
Fold: 1
Epoch: 019, Train Loss:, 0.7238
Epoch: 019, Train Acc: 0.3330
Epoch: 019, val Loss:, 0.7211
Epoch: 019, val Acc: 0.3333
 
Fold: 1
Epoch: 020, Train Loss:, 0.7268
Epoch: 020, Train Acc: 0.3330
Epoch: 020, val Loss:, 0.7078
Epoch: 020, val Acc: 0.3333
 
Fold: 1
Epoch: 021, Train Loss:, 0.7181
Epoch: 021, Train Acc: 0.3330
Epoch: 021, val Loss:, 0.7137
Epoch: 021, val Acc: 0.3333
 
Fold: 1
Epoch: 022, Train Loss:, 0.7099
Epoch: 022, Train Acc: 0.3330
Epoch: 022, val Loss:, 0.7286
Epoch: 022, val Acc: 0.3333
 
Fold: 1
Epoch: 023, Train Loss:, 0.7154
Epoch: 023, Train Acc: 0.3330
Epoch: 023, val Loss

Fold: 2
Epoch: 031, Train Loss:, 0.6952
Epoch: 031, Train Acc: 0.5486
Epoch: 031, val Loss:, 0.6890
Epoch: 031, val Acc: 0.5238
 
Fold: 2
Epoch: 032, Train Loss:, 0.7022
Epoch: 032, Train Acc: 0.6069
Epoch: 032, val Loss:, 0.6995
Epoch: 032, val Acc: 0.5714
 
Fold: 2
Epoch: 033, Train Loss:, 0.6842
Epoch: 033, Train Acc: 0.6617
Epoch: 033, val Loss:, 0.6863
Epoch: 033, val Acc: 0.6270
 
Fold: 2
Epoch: 034, Train Loss:, 0.6906
Epoch: 034, Train Acc: 0.7138
Epoch: 034, val Loss:, 0.6796
Epoch: 034, val Acc: 0.6349
 
Fold: 2
Epoch: 035, Train Loss:, 0.6880
Epoch: 035, Train Acc: 0.7677
Epoch: 035, val Loss:, 0.6961
Epoch: 035, val Acc: 0.6746
 
Fold: 2
Epoch: 036, Train Loss:, 0.6886
Epoch: 036, Train Acc: 0.7915
Epoch: 036, val Loss:, 0.6801
Epoch: 036, val Acc: 0.7143
 
Fold: 2
Epoch: 037, Train Loss:, 0.6869
Epoch: 037, Train Acc: 0.8048
Epoch: 037, val Loss:, 0.6930
Epoch: 037, val Acc: 0.7540
 
Fold: 2
Epoch: 038, Train Loss:, 0.6773
Epoch: 038, Train Acc: 0.8216
Epoch: 038, val Loss

Fold: 3
Epoch: 046, Train Loss:, 0.6620
Epoch: 046, Train Acc: 0.8401
Epoch: 046, val Loss:, 0.6837
Epoch: 046, val Acc: 0.7619
 
Fold: 3
Epoch: 047, Train Loss:, 0.6691
Epoch: 047, Train Acc: 0.8410
Epoch: 047, val Loss:, 0.6539
Epoch: 047, val Acc: 0.7619
 
Fold: 3
Epoch: 048, Train Loss:, 0.6590
Epoch: 048, Train Acc: 0.8339
Epoch: 048, val Loss:, 0.6701
Epoch: 048, val Acc: 0.7619
 
Fold: 3
Epoch: 049, Train Loss:, 0.6451
Epoch: 049, Train Acc: 0.8366
Epoch: 049, val Loss:, 0.6757
Epoch: 049, val Acc: 0.7619
 
Fold: 4
Epoch: 001, Train Loss:, 0.7934
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7704
Epoch: 001, val Acc: 0.3333
 
Fold: 4
Epoch: 002, Train Loss:, 0.7713
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7527
Epoch: 002, val Acc: 0.3333
 
Fold: 4
Epoch: 003, Train Loss:, 0.7596
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7570
Epoch: 003, val Acc: 0.3333
 
Fold: 4
Epoch: 004, Train Loss:, 0.7657
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss

...

[I 2024-08-04 00:07:00,688] Trial 68 finished with value: 0.74698 and parameters: {'learning_rate': 0.00014192452699927785, 'weight_decay': 0.00012168316396982381}. Best is trial 21 with value: 0.75144.


 
The average of mcc : 0.38618


C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  # This is added back by InteractiveShellApp.init_path()
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  if sys.path[0] == "":
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_la

Fold: 0
Epoch: 001, Train Loss:, 0.7915
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7605
Epoch: 001, val Acc: 0.3333
 
Fold: 0
Epoch: 002, Train Loss:, 0.7714
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7568
Epoch: 002, val Acc: 0.3333
 
Fold: 0
Epoch: 003, Train Loss:, 0.7599
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7527
Epoch: 003, val Acc: 0.3333
 
Fold: 0
Epoch: 004, Train Loss:, 0.7667
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss:, 0.7586
Epoch: 004, val Acc: 0.3333
 
Fold: 0
Epoch: 005, Train Loss:, 0.7704
Epoch: 005, Train Acc: 0.3330
Epoch: 005, val Loss:, 0.7455
Epoch: 005, val Acc: 0.3333
 
Fold: 0
Epoch: 006, Train Loss:, 0.7645
Epoch: 006, Train Acc: 0.3330
Epoch: 006, val Loss:, 0.7508
Epoch: 006, val Acc: 0.3333
 
Fold: 0
Epoch: 007, Train Loss:, 0.7611
Epoch: 007, Train Acc: 0.3330
Epoch: 007, val Loss:, 0.7380
Epoch: 007, val Acc: 0.3333
 
Fold: 0
Epoch: 008, Train Loss:, 0.7510
Epoch: 008, Train Acc: 0.3330
Epoch: 008, val Loss

Fold: 1
Epoch: 016, Train Loss:, 0.7320
Epoch: 016, Train Acc: 0.3330
Epoch: 016, val Loss:, 0.7266
Epoch: 016, val Acc: 0.3333
 
Fold: 1
Epoch: 017, Train Loss:, 0.7267
Epoch: 017, Train Acc: 0.3330
Epoch: 017, val Loss:, 0.7300
Epoch: 017, val Acc: 0.3333
 
Fold: 1
Epoch: 018, Train Loss:, 0.7207
Epoch: 018, Train Acc: 0.3330
Epoch: 018, val Loss:, 0.7131
Epoch: 018, val Acc: 0.3333
 
Fold: 1
Epoch: 019, Train Loss:, 0.7251
Epoch: 019, Train Acc: 0.3330
Epoch: 019, val Loss:, 0.7222
Epoch: 019, val Acc: 0.3333
 
Fold: 1
Epoch: 020, Train Loss:, 0.7276
Epoch: 020, Train Acc: 0.3330
Epoch: 020, val Loss:, 0.7089
Epoch: 020, val Acc: 0.3333
 
Fold: 1
Epoch: 021, Train Loss:, 0.7196
Epoch: 021, Train Acc: 0.3330
Epoch: 021, val Loss:, 0.7148
Epoch: 021, val Acc: 0.3333
 
Fold: 1
Epoch: 022, Train Loss:, 0.7111
Epoch: 022, Train Acc: 0.3330
Epoch: 022, val Loss:, 0.7299
Epoch: 022, val Acc: 0.3333
 
Fold: 1
Epoch: 023, Train Loss:, 0.7168
Epoch: 023, Train Acc: 0.3330
Epoch: 023, val Loss

In [ ]:
# start to optimize 
study = optuna.create_study(direction = 'maximize')
study.optimize(objective, n_trials=500)

study.best_params  

[I 2024-08-14 10:53:15,002] A new study created in memory with name: no-name-ab0cebcf-4d99-4070-9c32-c3006402ea7a
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  # This is added back by InteractiveShellApp.init_path()
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:22: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(s

Fold: 0
Epoch: 001, Train Loss:, 0.7916
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7606
Epoch: 001, val Acc: 0.3333
 
Fold: 0
Epoch: 002, Train Loss:, 0.7717
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7570
Epoch: 002, val Acc: 0.3333
 
Fold: 0
Epoch: 003, Train Loss:, 0.7603
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7530
Epoch: 003, val Acc: 0.3333
 
Fold: 0
Epoch: 004, Train Loss:, 0.7670
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss:, 0.7589
Epoch: 004, val Acc: 0.3333
 
Fold: 0
Epoch: 005, Train Loss:, 0.7708
Epoch: 005, Train Acc: 0.3330
Epoch: 005, val Loss:, 0.7459
Epoch: 005, val Acc: 0.3333
 
Fold: 0
Epoch: 006, Train Loss:, 0.7650
Epoch: 006, Train Acc: 0.3330
Epoch: 006, val Loss:, 0.7512
Epoch: 006, val Acc: 0.3333
 
Fold: 0
Epoch: 007, Train Loss:, 0.7615
Epoch: 007, Train Acc: 0.3330
Epoch: 007, val Loss:, 0.7385
Epoch: 007, val Acc: 0.3333
 
Fold: 0
Epoch: 008, Train Loss:, 0.7516
Epoch: 008, Train Acc: 0.3330
Epoch: 008, val Loss

Fold: 1
Epoch: 016, Train Loss:, 0.7327
Epoch: 016, Train Acc: 0.3330
Epoch: 016, val Loss:, 0.7273
Epoch: 016, val Acc: 0.3333
 
Fold: 1
Epoch: 017, Train Loss:, 0.7275
Epoch: 017, Train Acc: 0.3330
Epoch: 017, val Loss:, 0.7308
Epoch: 017, val Acc: 0.3333
 
Fold: 1
Epoch: 018, Train Loss:, 0.7218
Epoch: 018, Train Acc: 0.3330
Epoch: 018, val Loss:, 0.7140
Epoch: 018, val Acc: 0.3333
 
Fold: 1
Epoch: 019, Train Loss:, 0.7260
Epoch: 019, Train Acc: 0.3330
Epoch: 019, val Loss:, 0.7233
Epoch: 019, val Acc: 0.3333
 
Fold: 1
Epoch: 020, Train Loss:, 0.7291
Epoch: 020, Train Acc: 0.3330
Epoch: 020, val Loss:, 0.7100
Epoch: 020, val Acc: 0.3333
 
Fold: 1
Epoch: 021, Train Loss:, 0.7206
Epoch: 021, Train Acc: 0.3330
Epoch: 021, val Loss:, 0.7159
Epoch: 021, val Acc: 0.3333
 
Fold: 1
Epoch: 022, Train Loss:, 0.7122
Epoch: 022, Train Acc: 0.3330
Epoch: 022, val Loss:, 0.7310
Epoch: 022, val Acc: 0.3333
 
Fold: 1
Epoch: 023, Train Loss:, 0.7180
Epoch: 023, Train Acc: 0.3330
Epoch: 023, val Loss

Fold: 2
Epoch: 031, Train Loss:, 0.6983
Epoch: 031, Train Acc: 0.4293
Epoch: 031, val Loss:, 0.6917
Epoch: 031, val Acc: 0.4444
 
Fold: 2
Epoch: 032, Train Loss:, 0.7056
Epoch: 032, Train Acc: 0.5000
Epoch: 032, val Loss:, 0.7019
Epoch: 032, val Acc: 0.5000
 
Fold: 2
Epoch: 033, Train Loss:, 0.6874
Epoch: 033, Train Acc: 0.5786
Epoch: 033, val Loss:, 0.6889
Epoch: 033, val Acc: 0.5556
 
Fold: 2
Epoch: 034, Train Loss:, 0.6939
Epoch: 034, Train Acc: 0.6281
Epoch: 034, val Loss:, 0.6826
Epoch: 034, val Acc: 0.5873
 
Fold: 2
Epoch: 035, Train Loss:, 0.6912
Epoch: 035, Train Acc: 0.6811
Epoch: 035, val Loss:, 0.6988
Epoch: 035, val Acc: 0.6429
 
Fold: 2
Epoch: 036, Train Loss:, 0.6921
Epoch: 036, Train Acc: 0.7306
Epoch: 036, val Loss:, 0.6829
Epoch: 036, val Acc: 0.6349
 
Fold: 2
Epoch: 037, Train Loss:, 0.6909
Epoch: 037, Train Acc: 0.7721
Epoch: 037, val Loss:, 0.6960
Epoch: 037, val Acc: 0.6825
 
Fold: 2
Epoch: 038, Train Loss:, 0.6808
Epoch: 038, Train Acc: 0.7986
Epoch: 038, val Loss

Fold: 3
Epoch: 046, Train Loss:, 0.6666
Epoch: 046, Train Acc: 0.8410
Epoch: 046, val Loss:, 0.6867
Epoch: 046, val Acc: 0.7778
 
Fold: 3
Epoch: 047, Train Loss:, 0.6729
Epoch: 047, Train Acc: 0.8410
Epoch: 047, val Loss:, 0.6578
Epoch: 047, val Acc: 0.7698
 
Fold: 3
Epoch: 048, Train Loss:, 0.6636
Epoch: 048, Train Acc: 0.8330
Epoch: 048, val Loss:, 0.6737
Epoch: 048, val Acc: 0.7698
 
Fold: 3
Epoch: 049, Train Loss:, 0.6499
Epoch: 049, Train Acc: 0.8410
Epoch: 049, val Loss:, 0.6800
Epoch: 049, val Acc: 0.7619
 
Fold: 4
Epoch: 001, Train Loss:, 0.7936
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7705
Epoch: 001, val Acc: 0.3333
 
Fold: 4
Epoch: 002, Train Loss:, 0.7718
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7531
Epoch: 002, val Acc: 0.3333
 
Fold: 4
Epoch: 003, Train Loss:, 0.7603
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7576
Epoch: 003, val Acc: 0.3333
 
Fold: 4
Epoch: 004, Train Loss:, 0.7665
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss

...

C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  # This is added back by InteractiveShellApp.init_path()
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:22: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
C:\Users\USER\anaconda3\envs\toxpred\lib\site-packages\ipykernel_launcher.py:21: UserWarning: To cop

Fold: 0
Epoch: 001, Train Loss:, 0.7916
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7605
Epoch: 001, val Acc: 0.3333
 
Fold: 0
Epoch: 002, Train Loss:, 0.7716
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7569
Epoch: 002, val Acc: 0.3333
 
Fold: 0
Epoch: 003, Train Loss:, 0.7602
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7529
Epoch: 003, val Acc: 0.3333
 
Fold: 0
Epoch: 004, Train Loss:, 0.7670
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss:, 0.7588
Epoch: 004, val Acc: 0.3333
 
Fold: 0
Epoch: 005, Train Loss:, 0.7707
Epoch: 005, Train Acc: 0.3330
Epoch: 005, val Loss:, 0.7458
Epoch: 005, val Acc: 0.3333
 
Fold: 0
Epoch: 006, Train Loss:, 0.7649
Epoch: 006, Train Acc: 0.3330
Epoch: 006, val Loss:, 0.7511
Epoch: 006, val Acc: 0.3333
 
Fold: 0
Epoch: 007, Train Loss:, 0.7614
Epoch: 007, Train Acc: 0.3330
Epoch: 007, val Loss:, 0.7384
Epoch: 007, val Acc: 0.3333
 
Fold: 0
Epoch: 008, Train Loss:, 0.7515
Epoch: 008, Train Acc: 0.3330
Epoch: 008, val Loss

Fold: 1
Epoch: 016, Train Loss:, 0.7328
Epoch: 016, Train Acc: 0.3330
Epoch: 016, val Loss:, 0.7272
Epoch: 016, val Acc: 0.3333
 
Fold: 1
Epoch: 017, Train Loss:, 0.7275
Epoch: 017, Train Acc: 0.3330
Epoch: 017, val Loss:, 0.7307
Epoch: 017, val Acc: 0.3333
 
Fold: 1
Epoch: 018, Train Loss:, 0.7215
Epoch: 018, Train Acc: 0.3330
Epoch: 018, val Loss:, 0.7139
Epoch: 018, val Acc: 0.3333
 
Fold: 1
Epoch: 019, Train Loss:, 0.7259
Epoch: 019, Train Acc: 0.3330
Epoch: 019, val Loss:, 0.7231
Epoch: 019, val Acc: 0.3333
 
Fold: 1
Epoch: 020, Train Loss:, 0.7285
Epoch: 020, Train Acc: 0.3330
Epoch: 020, val Loss:, 0.7098
Epoch: 020, val Acc: 0.3333
 
Fold: 1
Epoch: 021, Train Loss:, 0.7206
Epoch: 021, Train Acc: 0.3330
Epoch: 021, val Loss:, 0.7157
Epoch: 021, val Acc: 0.3333
 
Fold: 1
Epoch: 022, Train Loss:, 0.7120
Epoch: 022, Train Acc: 0.3330
Epoch: 022, val Loss:, 0.7309
Epoch: 022, val Acc: 0.3333
 
Fold: 1
Epoch: 023, Train Loss:, 0.7178
Epoch: 023, Train Acc: 0.3330
Epoch: 023, val Loss

Fold: 2
Epoch: 031, Train Loss:, 0.6981
Epoch: 031, Train Acc: 0.4311
Epoch: 031, val Loss:, 0.6916
Epoch: 031, val Acc: 0.4444
 
Fold: 2
Epoch: 032, Train Loss:, 0.7054
Epoch: 032, Train Acc: 0.5159
Epoch: 032, val Loss:, 0.7017
Epoch: 032, val Acc: 0.5000
 
Fold: 2
Epoch: 033, Train Loss:, 0.6872
Epoch: 033, Train Acc: 0.5813
Epoch: 033, val Loss:, 0.6888
Epoch: 033, val Acc: 0.5635
 
Fold: 2
Epoch: 034, Train Loss:, 0.6937
Epoch: 034, Train Acc: 0.6334
Epoch: 034, val Loss:, 0.6823
Epoch: 034, val Acc: 0.5873
 
Fold: 2
Epoch: 035, Train Loss:, 0.6910
Epoch: 035, Train Acc: 0.6864
Epoch: 035, val Loss:, 0.6986
Epoch: 035, val Acc: 0.6429
 
Fold: 2
Epoch: 036, Train Loss:, 0.6919
Epoch: 036, Train Acc: 0.7367
Epoch: 036, val Loss:, 0.6826
Epoch: 036, val Acc: 0.6349
 
Fold: 2
Epoch: 037, Train Loss:, 0.6906
Epoch: 037, Train Acc: 0.7747
Epoch: 037, val Loss:, 0.6958
Epoch: 037, val Acc: 0.6825
 
Fold: 2
Epoch: 038, Train Loss:, 0.6806
Epoch: 038, Train Acc: 0.8004
Epoch: 038, val Loss

Fold: 3
Epoch: 046, Train Loss:, 0.6661
Epoch: 046, Train Acc: 0.8436
Epoch: 046, val Loss:, 0.6865
Epoch: 046, val Acc: 0.7698
 
Fold: 3
Epoch: 047, Train Loss:, 0.6726
Epoch: 047, Train Acc: 0.8392
Epoch: 047, val Loss:, 0.6574
Epoch: 047, val Acc: 0.7698
 
Fold: 3
Epoch: 048, Train Loss:, 0.6632
Epoch: 048, Train Acc: 0.8313
Epoch: 048, val Loss:, 0.6733
Epoch: 048, val Acc: 0.7698
 
Fold: 3
Epoch: 049, Train Loss:, 0.6494
Epoch: 049, Train Acc: 0.8401
Epoch: 049, val Loss:, 0.6796
Epoch: 049, val Acc: 0.7619
 
Fold: 4
Epoch: 001, Train Loss:, 0.7936
Epoch: 001, Train Acc: 0.3330
Epoch: 001, val Loss:, 0.7705
Epoch: 001, val Acc: 0.3333
 
Fold: 4
Epoch: 002, Train Loss:, 0.7717
Epoch: 002, Train Acc: 0.3330
Epoch: 002, val Loss:, 0.7530
Epoch: 002, val Acc: 0.3333
 
Fold: 4
Epoch: 003, Train Loss:, 0.7602
Epoch: 003, Train Acc: 0.3330
Epoch: 003, val Loss:, 0.7575
Epoch: 003, val Acc: 0.3333
 
Fold: 4
Epoch: 004, Train Loss:, 0.7664
Epoch: 004, Train Acc: 0.3330
Epoch: 004, val Loss